In [1]:
!git clone https://github.com/mueedurrehman/distiller.git
%cd distiller
!pip3 install -e .

Cloning into 'distiller'...
remote: Enumerating objects: 11, done.
remote: Counting objects: 100% (11/11), done.
remote: Compressing objects: 100% (7/7), done.
remote: Total 6174 (delta 4), reused 6 (delta 4), pack-reused 6163
Receiving objects: 100% (6174/6174), 39.83 MiB | 35.22 MiB/s, done.
Resolving deltas: 100% (4327/4327), done.
/content/distiller
Obtaining file:///content/distiller
     |████████████████████████████████| 2.1MB 18.9MB/s 
     |████████████████████████████████| 734.6MB 25kB/s 
     |████████████████████████████████| 10.2MB 41.4MB/s 
     |████████████████████████████████| 460kB 56.7MB/s 
     |████████████████████████████████| 110.5MB 37kB/s 
     |████████████████████████████████| 51kB 8.7MB/s 
     |████████████████████████████████| 798kB 50.5MB/s 
     |████████████████████████████████| 112kB 59.0MB/s 
     |████████████████████████████████| 1.7MB 51.0MB/s 
     |████████████████████████████████| 235kB 66.6MB/s 
     |████████████████████████████████| 153kB 65.

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [3]:
import torch
import torchvision
import torchvision.transforms as transforms
import torchvision.models as models
from torchsummary import summary
import matplotlib.pyplot as plt
import numpy as np
import torch.nn as nn
import torch.nn.functional as F
import time
import math
import yaml
import distiller
from collections import OrderedDict
import os
import pandas as pd

In [4]:
!cp "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Baseline Models/baseResnet56" .
# !cp ../../../drive/MyDrive/CS6787\ -\ Final\ Project/Google\ Colab\ Scripts/Quantization\ Models/Resnet56\ Quantization\ Stats/resnet56_quant_stats.yaml .

Asymmetric U

In [12]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/4bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  109.28559 |   63.82626 |   63.82626 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |    1.15427 |   -6.96875 |    6.96875 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |    0.04471 |   -0.00244 |    0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          28475 |    0.00000 |    0.00000 |  1.56250 |  2.12402 |  0.00000 |   22.75662 |    0.04510 |   -0.00248 |    0.03276 |
| 174 | module.layer3.2.conv1.weight_scale             | (64, 1, 1, 1)  |    

In [19]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/6bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |   459.15414 |  268.11420 |  268.11420 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |     4.85739 |  -29.34375 |   29.34375 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |     0.04471 |   -0.00243 |    0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          34370 |    0.00000 |    0.00000 |  0.00000 |  1.51367 |  0.00000 |    6.76541 |     0.04474 |   -0.00243 |    0.03314 |
| 174 | module.layer3.2.conv1.weight_scale             | (64, 1, 1, 1)  |

In [20]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/8bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  1859.78979 |  1085.35242 |  1085.35242 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |    19.29917 |  -118.95312 |   118.95312 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |     0.04471 |    -0.00243 |     0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          36026 |    0.00000 |    0.00000 |  0.00000 |  0.21973 |  0.00000 |    2.27322 |     0.04471 |    -0.00243 |     0.03317 |
| 174 | module.layer3.2.conv1.weight_scale             | (64, 1, 

In [15]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/10bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  29871.72266 |  17430.29297 |  17430.29297 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |    309.65143 |  -1910.43750 |   1910.43750 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |      0.04471 |     -0.00243 |      0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          36811 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.14377 |      0.04471 |     -0.00243 |      0.03317 |
| 174 | module.layer3.2.conv1.weight_scale           

In [16]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/12bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  29851.16406 |  17427.58203 |  17427.58203 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |    309.77200 |  -1910.37500 |   1910.37500 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |      0.04471 |     -0.00243 |      0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          36813 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.13835 |      0.04471 |     -0.00243 |      0.03317 |
| 174 | module.layer3.2.conv1.weight_scale           

In [17]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/14bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  119387.34375 |   69717.78906 |   69717.78906 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |    1239.30151 |   -7643.00000 |    7643.00000 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |       0.04471 |      -0.00243 |       0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          36849 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.04069 |       0.04471 |      -0.00243 |       0.03317 |
| 174 | module.layer3.2.conv1.weight_scal

In [18]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/16bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |   477632.84375 |  278895.78125 |  278895.78125 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |     4957.36963 |  -30573.32812 |   30573.32812 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |        0.04471 |      -0.00243 |       0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          36859 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.01356 |        0.04471 |      -0.00243 |       0.03317 |
| 174 | module.layer3.2.conv1.weight_